# Setting Up All Artifacts details

In [9]:
## Give appropriate permission to the directory "FOLDER_WITH_ARTIFACTS" you are working with
import os
os.environ['QNN_SDK_ROOT']="/opt/qcom/aistack/qairt/2.25.0.240728"#set up your snpe path here.
os.environ['SNPE_ROOT']="/opt/qcom/aistack/qairt/2.25.0.240728"
os.environ['ANDROID_NDK_ROOT']="/opt/Android/Ndk/android-ndk-r23c" #"/usr/android-ndk-r26c"#set up your snpe path here.
os.environ['QNN_TARGET_ARCH']="aarch64-android"

In [5]:
## Note- Use python3.8 or above for generating onnx
!pip install super-gradients==3.1.2
import torch
from super_gradients.training import models
from super_gradients.common.object_names import Models
import cv2
import numpy as np
import os

Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://mirrors.aliyun.com/pypi/simple


## Getting the ONNX Model

In [6]:
os.makedirs('models', exist_ok=True)

In [13]:
model = models.get(Models.YOLO_NAS_S, pretrained_weights="coco")
# Prpare model for conversion
# Input size is in format of [Batch x Channels x Width x Height] where 640 is the standard COCO dataset dimensions
model.eval()
model.prep_model_for_conversion(input_size=[1, 3, 320, 320])
# Create dummy_input
dummy_input = torch.randn([1, 3, 320, 320], device="cpu")
# Convert model to onnx
torch.onnx.export(model, dummy_input, "./models/yolo_nas_s.onnx", opset_version=11)

[2025-02-22 15:14:33] INFO - checkpoint_utils.py - License Notification: YOLO-NAS pre-trained weights are subjected to the specific license terms and conditions detailed in 
https://github.com/Deci-AI/super-gradients/blob/master/LICENSE.YOLONAS.md
By downloading the pre-trained weight files you agree to comply with these terms.


#### Getting the FP32 Model

In [15]:
%%bash
source $SNPE_ROOT/bin/envsetup.sh
export PATH=${ANDROID_NDK_ROOT}:${PATH}
qnn-onnx-converter --input_network ./models/yolo_nas_s.onnx --output_path output_cpu/yolo_nas_s.cpp --out_node 887 --out_node 879
qnn-model-lib-generator -c output_cpu/yolo_nas_s.cpp -b output_cpu/yolo_nas_s.bin --output_dir output_cpu/ -t aarch64-android

[INFO] AISW SDK environment set
[INFO] QNN_SDK_ROOT: /media/code/opt/qcom/aistack/qairt/2.25.0.240728
[INFO] SNPE_ROOT: /media/code/opt/qcom/aistack/qairt/2.25.0.240728


2025-02-22 16:20:55,405 - 235 - INFO - Simplified model validation is successful
2025-02-22 16:20:57,287 - 235 - INFO - user_provided_output is same as graph_output..skipping update_output_names call
2025-02-22 16:20:59,708 - 235 - INFO - Skipping quantization, no input_list provided
2025-02-22 16:20:59,708 - 235 - INFO - Saving QNN Model...
2025-02-22 16:20:59,808 - 235 - INFO - Model CPP saved at: output_cpu/yolo_nas_s.cpp 
2025-02-22 16:21:00,043 - 235 - INFO - Model BIN saved at: /media/code/qnn/qidk/Solutions/QNN/VisionSolution1-ObjectDetection-YoloNas/output_cpu/yolo_nas_s.bin 
2025-02-22 16:21:00,134 - 235 - INFO - Conversion complete!
2025-02-22 16:21:00,309 -    INFO - qnn-model-lib-generator: Model cpp file path  : output_cpu/yolo_nas_s.cpp
2025-02-22 16:21:00,309 -    INFO - qnn-model-lib-generator: Model bin file path  : output_cpu/yolo_nas_s.bin
2025-02-22 16:21:00,309 -    INFO - qnn-model-lib-generator: Library target       : [['aarch64-android']]
2025-02-22 16:21:00,309

     {.scalarParam= (Qnn_Scalar_t) {QNN_DATATYPE_UINT_32, {.uint32Value = 1}}}}
     ^~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s.cpp:23512:30: warning: mixture of designated and non-designated initializers in the same initializer list is a C99 extension [-Wc99-designator]
                             .hybridCoo= {.numSpecifiedElements= 0, .numSparseDimensions= 0}},
                             ^~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s.cpp:23511:30: note: first non-designated initializer is here
            .sparseParams= { QNN_SPARSE_LAYOUT_UNDEFINED,
                             ^~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s.cpp:23497:13: warning: mixture of designated and non-designated initializers in the same initializer list is a C99 extension [-Wc99-designator]
            .id=0,
            ^~~~~
jni/yolo_nas_s.cpp:23508:13: note: first non-designated initializer is here
            {.clientBuf= { .dat

#### Getting the Quatized Model for DSP

In [16]:
%%bash
mkdir -p raw

In [18]:
import cv2
import numpy as np
import os

def preprocess(original_image):
    resized_image = cv2.resize(original_image, (320, 320))
    resized_image = resized_image/255
    return resized_image

##Please download Coco2014 dataset and give the path here
dataset_path = "images/"

filenames=[]
for path in os.listdir(dataset_path):
    # check if current path is a file
    if os.path.isfile(os.path.join(dataset_path, path)):
        filenames.append(os.path.join(dataset_path, path))
        
for filename in filenames:
    original_image = cv2.imread(filename)
    img = preprocess(original_image)
    img = img.astype(np.float32)
    img.tofile("raw/"+filename.split("/")[-1].split(".")[0]+".raw")


In [19]:
%%bash
find raw -name *.raw > input.txt
cat input.txt

In [20]:
%%bash
source $SNPE_ROOT/bin/envsetup.sh
export PATH=${ANDROID_NDK_ROOT}:${PATH}
qnn-onnx-converter --input_network models/yolo_nas_s.onnx --output_path output_dsp/yolo_nas_s_quantized.cpp --out_node 887 --out_node 879 --input_list input.txt 
qnn-model-lib-generator -c output_dsp/yolo_nas_s_quantized.cpp -b output_dsp/yolo_nas_s_quantized.bin --output_dir output_dsp/ -t aarch64-android
mv output_dsp/aarch64-android/libyolo_nas_s_quantized.so  output_dsp/aarch64-android/libyolo_nas_w8a8_dsp.so 

raw/000000364587.raw
raw/000000333745.raw
raw/000000370711.raw
raw/000000131556.raw
raw/000000557884.raw
raw/000000152771.raw
raw/000000290833.raw
raw/000000565597.raw
raw/000000090956.raw
raw/000000061108.raw
raw/000000579158.raw
raw/000000146825.raw
raw/000000329614.raw
raw/000000036861.raw
raw/000000530854.raw
raw/000000460929.raw
raw/000000323709.raw
raw/000000519569.raw
raw/000000079969.raw
raw/000000464251.raw
raw/000000189078.raw
raw/000000337498.raw
raw/000000459757.raw
raw/000000148662.raw
raw/000000110042.raw
raw/000000434996.raw
raw/000000017627.raw
raw/000000104603.raw
raw/000000546219.raw
raw/000000047112.raw
raw/000000015335.raw
raw/000000013004.raw
raw/000000526197.raw
raw/000000214869.raw
raw/000000243344.raw
raw/000000083531.raw
raw/000000301135.raw
raw/000000018575.raw
raw/000000086755.raw
raw/000000462031.raw
raw/000000386352.raw
raw/000000237864.raw
raw/000000197022.raw
raw/000000173302.raw
raw/000000350122.raw
raw/000000392722.raw
raw/000000395701.raw
raw/000000163

[INFO] AISW SDK environment set
[INFO] QNN_SDK_ROOT: /media/code/opt/qcom/aistack/qairt/2.25.0.240728
[INFO] SNPE_ROOT: /media/code/opt/qcom/aistack/qairt/2.25.0.240728


2025-02-22 16:46:05,481 - 235 - INFO - Simplified model validation is successful
2025-02-22 16:46:07,614 - 235 - INFO - user_provided_output is same as graph_output..skipping update_output_names call


    48.1ms [  INFO ] Inferences will run in sync mode
    55.0ms [  INFO ] Initializing logging in the backend. Callback: [0x7f0613496770], Log Level: [3]
    55.0ms [  INFO ] No BackendExtensions lib provided;initializing NetRunBackend Interface
    13.2ms [  INFO ] [QNN_CPU] CpuBackend creation start
    13.3ms [  INFO ] [QNN_CPU] CpuBackend creation end
    68.3ms [WARNING] Unable to find a device with NetRunDeviceKeyDefault in Library NetRunBackendLibKeyDefault
    68.3ms [WARNING] Profile Logger with name = defaultKey doesn't exist! Returning nullptr
    13.3ms [  INFO ] [QNN_CPU] QnnContext create start
    13.3ms [  INFO ] [QNN_CPU] QnnContext create end
    68.6ms [  INFO ] Entering QuantizeRuntimeApp flow
    68.6ms [WARNING] Profile Logger with name = defaultKey doesn't exist! Returning nullptr
    13.7ms [  INFO ] [QNN_CPU] CpuGraph creation start
    13.8ms [  INFO ] [QNN_CPU] CpuGraph creation end
    13.8ms [  INFO ] [QNN_CPU] QnnGraph create end
    78.1ms [  INFO ] [QNN

2025-02-22 17:14:27,220 - 235 - INFO - Saving QNN Model...
2025-02-22 17:14:27,270 - 235 - INFO - Model CPP saved at: output_dsp/yolo_nas_s_quantized.cpp 
2025-02-22 17:14:27,270 - 235 - INFO - Model BIN saved at: /media/code/qnn/qidk/Solutions/QNN/VisionSolution1-ObjectDetection-YoloNas/output_dsp/yolo_nas_s_quantized.bin 
2025-02-22 17:14:27,276 - 235 - INFO - Conversion complete!
2025-02-22 17:14:27,600 -    INFO - qnn-model-lib-generator: Model cpp file path  : output_dsp/yolo_nas_s_quantized.cpp
2025-02-22 17:14:27,600 -    INFO - qnn-model-lib-generator: Model bin file path  : output_dsp/yolo_nas_s_quantized.bin
2025-02-22 17:14:27,600 -    INFO - qnn-model-lib-generator: Library target       : [['aarch64-android']]
2025-02-22 17:14:27,600 -    INFO - qnn-model-lib-generator: Library name         : yolo_nas_s_quantized
2025-02-22 17:14:27,600 -    INFO - qnn-model-lib-generator: Output directory     : output_dsp
2025-02-22 17:14:27,600 -    INFO - qnn-model-lib-generator: Output 

jni/yolo_nas_s_quantized.cpp:21767:6: warning: mixture of designated and non-designated initializers in the same initializer list is a C99 extension [-Wc99-designator]
    {.paramType=QNN_PARAMTYPE_TENSOR,
     ^~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s_quantized.cpp:21769:6: note: first non-designated initializer is here
     {.tensorParam=(Qnn_Tensor_t) {
     ^~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s_quantized.cpp:21809:30: warning: mixture of designated and non-designated initializers in the same initializer list is a C99 extension [-Wc99-designator]
                             .hybridCoo= {.numSpecifiedElements= 0, .numSparseDimensions= 0}},
                             ^~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s_quantized.cpp:21808:30: note: first non-designated initializer is here
            .sparseParams= { QNN_SPARSE_LAYOUT_UNDEFINED,
                             ^~~~~~~~~~~~~~~~~~~~~~~~~~~
jni/yolo_nas_s_quantized.cpp:21794:13: war